# Tutorial: Evaluating RAG Pipelines

- **Level**: Intermediate
- **Time to complete**: 15 minutes
- **Components Used**: `InMemoryDocumentStore`, `InMemoryEmbeddingRetriever`, `ChatPromptBuilder`, `OpenAIChatGenerator`, `DocumentMRREvaluator`, `FaithfulnessEvaluator`, `SASEvaluator`
- **Prerequisites**: You must have an API key from an active OpenAI account as this tutorial is using the gpt-4o-mini model by OpenAI: https://platform.openai.com/api-keys
- **Goal**: After completing this tutorial, you'll have learned how to evaluate your RAG pipelines both with model-based, and statistical metrics available in the Haystack evaluation offering. You'll also see which other evaluation frameworks are integrated with Haystack.

> This tutorial uses the latest version of Haystack 2.x (`haystack-ai`). For more information on Haystack 2.0, read the [Haystack 2.0 announcement](https://haystack.deepset.ai/blog/haystack-2-release) or visit the [Haystack Documentation](https://docs.haystack.deepset.ai/docs/intro).

## Overview

In this tutorial, you will learn how to evaluate Haystack pipelines, in particular, Retriaval-Augmented Generation ([RAG](https://www.deepset.ai/blog/llms-retrieval-augmentation)) pipelines.
1. You will first build a pipeline that answers medical questions based on PubMed data.
2. You will build an evaluation pipeline that makes use of some metrics like Document MRR and Answer Faithfulness.
3. You will run your RAG pipeline and evaluated the output with your evaluation pipeline.

Haystack provides a wide range of [`Evaluators`](https://docs.haystack.deepset.ai/docs/evaluators) which can perform 2 types of evaluations:
- [Model-Based evaluation](https://docs.haystack.deepset.ai/docs/model-based-evaluation)
- [Statistical evaluation](https://docs.haystack.deepset.ai/docs/statistical-evaluation)

We will use some of these evalution techniques in this tutorial to evaluate a RAG pipeline that is designed to answer questions on PubMed data.

>🧑‍🍳 As well as Haystack's own evaluation metrics, you can also integrate with a number of evaluation frameworks. See the integrations and examples below 👇
> - [Evaluate with DeepEval](https://colab.research.google.com/github/deepset-ai/haystack-cookbook/blob/main/notebooks/rag_eval_deep_eval.ipynb)
> - [Evaluate with RAGAS](https://colab.research.google.com/github/deepset-ai/haystack-cookbook/blob/main/notebooks/rag_eval_ragas.ipynb)
> - [Evaluate with UpTrain](https://colab.research.google.com/github/deepset-ai/haystack-cookbook/blob/main/notebooks/rag_eval_uptrain.ipynb)

### Evaluating RAG Pipelines
RAG pipelines ultimately consist of at least 2 steps:
- Retrieval
- Generation

To evaluate a full RAG pipeline, we have to evaluate each of these steps in isolation, as well as a full unit. While retrieval can in some cases be evaluated with some statistical metrics that require labels, it's not a straight-forward task to do the same for the generation step. Instead, we often rely on model-based metrics to evaluate the generation step, where an LLM is used as the 'evaluator'.

![Steps or RAG](https://raw.githubusercontent.com/deepset-ai/haystack-tutorials/main/tutorials/img/tutorial35_rag.png)

#### 📺 Code Along

<iframe width="560" height="315" src="https://www.youtube.com/embed/5PrzXaZ0-qk?si=lgBSfHatbV2i59J-" title="YouTube video player" frameborder="0" allow="accelerometer; autoplay; clipboard-write; encrypted-media; gyroscope; picture-in-picture; web-share" referrerpolicy="strict-origin-when-cross-origin" allowfullscreen></iframe>


## Preparing the Colab Environment

- [Enable GPU Runtime in Colab](https://docs.haystack.deepset.ai/docs/enabling-gpu-acceleration)
- [Set logging level to INFO](https://docs.haystack.deepset.ai/docs/setting-the-log-level)

## Installing Haystack

Install Haystack and [datasets](https://pypi.org/project/datasets/) with `pip`:

In [ ]:
%%bash

pip install haystack-ai
pip install "datasets>=2.6.1"
pip install "sentence-transformers>=3.0.0"

### Enabling Telemetry

Knowing you're using this tutorial helps us decide where to invest our efforts to build a better product but you can always opt out by commenting the following line. See [Telemetry](https://docs.haystack.deepset.ai/docs/enabling-telemetry) for more details.

In [2]:
from haystack.telemetry import tutorial_running

tutorial_running(35)

/Users/amna.mubashar/Library/Python/3.9/lib/python/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


## Create the RAG Pipeline to Evaluate

To evaluate a RAG pipeline, we need a RAG pipeline to start with. So, we will start by creating a question answering pipeline.

> 💡 For a complete tutorial on creating Retrieval-Augmmented Generation pipelines check out the [Creating Your First QA Pipeline with Retrieval-Augmentation Tutorial](https://haystack.deepset.ai/tutorials/27_first_rag_pipeline)

For this tutorial, we will be using [a labeled PubMed dataset](https://huggingface.co/datasets/vblagoje/PubMedQA_instruction/viewer/default/train?row=0) with questions, contexts and answers. This way, we can use the contexts as Documents, and we also have the required labeled data that we need for some of the evaluation metrics we will be using.

First, let's fetch the prepared dataset and extract `all_documents`, `all_questions` and `all_ground_truth_answers`:

> ℹ️ The dataset is quite large, we're using the first 1000 rows in this example, but you can increase this if you want to


In [3]:
from datasets import load_dataset
from haystack import Document

dataset = load_dataset("vblagoje/PubMedQA_instruction", split="train")
dataset = dataset.select(range(1000))
all_documents = [Document(content=doc["context"]) for doc in dataset]
all_questions = [doc["instruction"] for doc in dataset]
all_ground_truth_answers = [doc["response"] for doc in dataset]

Generating test split: 100%|██████████| 1000/1000 [00:00<00:00, 287025.53 examples/s]


Next, let's build a simple indexing pipeline and write the `documents` into a DocumentStore. Here, we're using the `InMemoryDocumentStore`.

> `InMemoryDocumentStore` is the simplest DocumentStore to get started with. It requires no external dependencies and it's a good option for smaller projects and debugging. But it doesn't scale up so well to larger Document collections, so it's not a good choice for production systems. To learn more about the different types of external databases that Haystack supports, see [DocumentStore Integrations](https://haystack.deepset.ai/integrations?type=Document+Store).

In [4]:
from typing import List
from haystack import Pipeline
from haystack.components.embedders import SentenceTransformersDocumentEmbedder
from haystack.components.writers import DocumentWriter
from haystack.document_stores.in_memory import InMemoryDocumentStore
from haystack.document_stores.types import DuplicatePolicy

document_store = InMemoryDocumentStore()

document_embedder = SentenceTransformersDocumentEmbedder(model="sentence-transformers/all-MiniLM-L6-v2")
document_writer = DocumentWriter(document_store=document_store, policy=DuplicatePolicy.SKIP)

indexing = Pipeline()
indexing.add_component(instance=document_embedder, name="document_embedder")
indexing.add_component(instance=document_writer, name="document_writer")

indexing.connect("document_embedder.documents", "document_writer.documents")

indexing.run({"document_embedder": {"documents": all_documents}})

/Users/amna.mubashar/Library/Python/3.9/lib/python/site-packages/huggingface_hub/file_download.py:1132: FutureWarning: `resume_download` is deprecated and will be removed in version 1.0.0. Downloads always resume when possible. If you want to force a new download, use `force_download=True`.
  warnings.warn(
Batches: 100%|██████████| 32/32 [00:08<00:00,  3.99it/s]


{'document_writer': {'documents_written': 1000}}

Now that we have our data ready, we can create a simple RAG pipeline.

In this example, we'll be using:
- [`InMemoryEmbeddingRetriever`](https://docs.haystack.deepset.ai/docs/inmemoryembeddingretriever) which will get the relevant documents to the query.
- [`OpenAIChatGenerator`](https://docs.haystack.deepset.ai/docs/OpenAIChatGenerator) to generate answers to queries. You can replace `OpenAIChatGenerator` in your pipeline with another `ChatGenerator`. Check out the full list of generators [here](https://docs.haystack.deepset.ai/docs/generators).

In [8]:
import os
from getpass import getpass
from haystack.components.builders import AnswerBuilder, ChatPromptBuilder
from haystack.dataclasses import ChatMessage
from haystack.components.embedders import SentenceTransformersTextEmbedder
from haystack.components.generators.chat import OpenAIChatGenerator
from haystack.components.retrievers.in_memory import InMemoryEmbeddingRetriever

if "OPENAI_API_KEY" not in os.environ:
    os.environ["OPENAI_API_KEY"] = getpass("Enter OpenAI API key:")

template = [
    ChatMessage.from_user(
        """
        You have to answer the following question based on the given context information only.

        Context:
        {% for document in documents %}
            {{ document.content }}
        {% endfor %}

        Question: {{question}}
        Answer:
        """
    )
]

rag_pipeline = Pipeline()
rag_pipeline.add_component(
    "query_embedder", SentenceTransformersTextEmbedder(model="sentence-transformers/all-MiniLM-L6-v2")
)
rag_pipeline.add_component("retriever", InMemoryEmbeddingRetriever(document_store, top_k=3))
rag_pipeline.add_component("prompt_builder", ChatPromptBuilder(template=template))
rag_pipeline.add_component("generator", OpenAIChatGenerator(model="gpt-4o-mini"))
rag_pipeline.add_component("answer_builder", AnswerBuilder())

rag_pipeline.connect("query_embedder", "retriever.query_embedding")
rag_pipeline.connect("retriever", "prompt_builder.documents")
rag_pipeline.connect("prompt_builder.prompt", "generator.messages")
rag_pipeline.connect("generator.replies", "answer_builder.replies")
rag_pipeline.connect("retriever", "answer_builder.documents")

🚅 Components
  - query_embedder: SentenceTransformersTextEmbedder
  - retriever: InMemoryEmbeddingRetriever
  - prompt_builder: ChatPromptBuilder
  - generator: OpenAIChatGenerator
  - answer_builder: AnswerBuilder
🛤️ Connections
  - query_embedder.embedding -> retriever.query_embedding (List[float])
  - retriever.documents -> prompt_builder.documents (List[Document])
  - retriever.documents -> answer_builder.documents (List[Document])
  - prompt_builder.prompt -> generator.messages (List[ChatMessage])
  - generator.replies -> answer_builder.replies (List[ChatMessage])

### Asking a Question

When asking a question, use the `run()` method of the pipeline. Make sure to provide the question to all components that require it as input. In this case these are the `query_embedder`, the `prompt_builder` and the `answer_builder`.

In [9]:
question = "Do high levels of procalcitonin in the early phase after pediatric liver transplantation indicate poor postoperative outcome?"

response = rag_pipeline.run(
    {
        "query_embedder": {"text": question},
        "prompt_builder": {"question": question},
        "answer_builder": {"query": question},
    }
)
print(response["answer_builder"]["answers"][0].data)

Batches: 100%|██████████| 1/1 [00:02<00:00,  2.85s/it]
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)


Yes, high levels of procalcitonin in the early phase after pediatric liver transplantation indicate poor postoperative outcomes. Patients with elevated PCT levels on postoperative day 2 had higher International Normalized Ratio values on postoperative day 5, suffered more often from primary graft non-function, and had longer stays in the pediatric intensive care unit and on mechanical ventilation.


## Evaluate the Pipeline

For this tutorial, let's evaluate the pipeline with the following metrics:

- [Document Mean Reciprocal Rank](https://docs.haystack.deepset.ai/docs/documentmrrevaluator): Evaluates retrieved documents using ground truth labels. It checks at what rank ground truth documents appear in the list of retrieved documents.
- [Semantic Answer Similarity](https://docs.haystack.deepset.ai/docs/sasevaluator): Evaluates predicted answers using ground truth labels. It checks the semantic similarity of a predicted answer and the ground truth answer using a fine-tuned language model.
- [Faithfulness](https://docs.haystack.deepset.ai/docs/faithfulnessevaluator): Uses an LLM to evaluate whether a generated answer can be inferred from the provided contexts. Does not require ground truth labels.


Firt, let's actually run our RAG pipeline with a set of questions, and make sure we have the ground truth labels (both answers and documents) for these questions. Let's start with 25 random questions and labels 👇

> 📝 **Some Notes:**
> 1. For a full list of available metrics, check out the [Haystack Evaluators](https://docs.haystack.deepset.ai/docs/evaluators).
> 2. In our dataset, for each example question, we have 1 ground truth document as labels. However, in some scenarios more than 1 ground truth document may be provided as labels. You will notice that this is why we provide a list of `ground_truth_documents` for each question.

In [10]:
import random

questions, ground_truth_answers, ground_truth_docs = zip(
    *random.sample(list(zip(all_questions, all_ground_truth_answers, all_documents)), 25)
)

Next, let's run our pipeline and make sure to track what our pipeline returns as answers, and which documents it retrieves:

In [11]:
rag_answers = []
retrieved_docs = []

for question in list(questions):
    response = rag_pipeline.run(
        {
            "query_embedder": {"text": question},
            "prompt_builder": {"question": question},
            "answer_builder": {"query": question},
        }
    )
    print(f"Question: {question}")
    print("Answer from pipeline:")
    print(response["answer_builder"]["answers"][0].data)
    print("\n-----------------------------------\n")

    rag_answers.append(response["answer_builder"]["answers"][0].data)
    retrieved_docs.append(response["answer_builder"]["answers"][0].documents)

Batches: 100%|██████████| 1/1 [00:00<00:00,  2.89it/s]


Question: Is higher fibrinogen level independently linked with the presence and severity of new-onset coronary atherosclerosis among Han Chinese population?
Answer from pipeline:
Yes, higher fibrinogen level is independently linked with the presence and severity of new-onset coronary atherosclerosis among the Han Chinese population. The study demonstrated that plasma fibrinogen level was independently associated with high Gensini score (GS) and the presence of coronary atherosclerosis after adjusting for potential confounders.

-----------------------------------



Batches: 100%|██████████| 1/1 [00:00<00:00,  5.88it/s]


Question: Are successional changes in the chicken cecal microbiome during 42 days of growth independent of organic acid feed additives?
Answer from pipeline:
Yes, successional changes in the chicken cecal microbiome during the 42 days of growth are independent of organic acid feed additives. The study found that treatment effects on specific pathogens and the cecal microbiome as a whole were generally non-significant, while temporal changes in the cecal microbiome were dramatic, highly significant, and consistent across treatments, indicating that these changes occur regardless of the presence of the organic acids.

-----------------------------------



Batches: 100%|██████████| 1/1 [00:00<00:00,  8.13it/s]


...

Question: Is the ADAMTS13-von Willebrand factor axis involved in the pathophysiology of kidney ischemia-reperfusion injury?
Answer from pipeline:
Yes, the ADAMTS13-von Willebrand factor axis is involved in the pathophysiology of kidney ischemia-reperfusion injury, as indicated by the significant changes in ADAMTS13 and vWF levels and the associated kidney damage observed in the study.

-----------------------------------



Batches: 100%|██████████| 1/1 [00:00<00:00, 40.44it/s]


Question: Is repeat endoscopic ultrasound fine needle aspiration after a first negative procedure useful in pancreatic lesions?
Answer from pipeline:
Yes, repeat endoscopic ultrasound fine needle aspiration (EUS-FNA) after a first negative procedure can be useful in pancreatic lesions. In the study, the diagnostic yield of the second EUS-FNA was 58.8%, which contributed to an overall diagnostic yield increase to 86.3% for all patients. The likelihood of a positive diagnosis with the second EUS-FNA was particularly higher in patients who had an "atypical" histological result from the first EUS-FNA compared to those who had a "normal" result. This suggests that repeating the procedure may help to obtain a definitive diagnosis in cases that were inconclusive initially.

-----------------------------------



Batches: 100%|██████████| 1/1 [00:00<00:00, 12.62it/s]


Question: Does tRAIL receptor deletion in mice suppress the inflammation of nutrient excess?
Answer from pipeline:
Yes, TRAIL receptor deletion in mice suppresses the inflammation associated with nutrient excess. In the study, TR knockout (TR(-/-)) mice showed reduced weight gain, adiposity, and insulin resistance when fed a high-fat, cholesterol, and fructose (FFC) diet. Additionally, these mice exhibited suppressed steatohepatitis and diminished accumulation and activation of inflammatory macrophages in the liver and adipose tissue, indicating a significant reduction in inflammation related to nutrient excess.

-----------------------------------



While each evaluator is a component that can be run individually in Haystack, they can also be added into a pipeline. This way, we can construct an `eval_pipeline` that includes all evaluators for the metrics we want to evaluate our pipeline on.

In [12]:
from haystack.components.evaluators.document_mrr import DocumentMRREvaluator
from haystack.components.evaluators.faithfulness import FaithfulnessEvaluator
from haystack.components.evaluators.sas_evaluator import SASEvaluator

eval_pipeline = Pipeline()
eval_pipeline.add_component("doc_mrr_evaluator", DocumentMRREvaluator())
eval_pipeline.add_component("faithfulness", FaithfulnessEvaluator())
eval_pipeline.add_component("sas_evaluator", SASEvaluator(model="sentence-transformers/all-MiniLM-L6-v2"))

results = eval_pipeline.run(
    {
        "doc_mrr_evaluator": {
            "ground_truth_documents": list([d] for d in ground_truth_docs),
            "retrieved_documents": retrieved_docs,
        },
        "faithfulness": {
            "questions": list(questions),
            "contexts": list([d.content] for d in ground_truth_docs),
            "predicted_answers": rag_answers,
        },
        "sas_evaluator": {"predicted_answers": rag_answers, "ground_truth_answers": list(ground_truth_answers)},
    }
)

/Users/amna.mubashar/Library/Python/3.9/lib/python/site-packages/huggingface_hub/file_download.py:1132: FutureWarning: `resume_download` is deprecated and will be removed in version 1.0.0. Downloads always resume when possible. If you want to force a new download, use `force_download=True`.
  warnings.warn(
100%|██████████| 25/25 [00:46<00:00,  1.87s/it]


### Constructing an Evaluation Report

Once we've run our evaluation pipeline, we can also create a full evaluation report. Haystac provides an `EvaluationRunResult` which we can use to display a `score_report` 👇

In [13]:
from haystack.evaluation.eval_run_result import EvaluationRunResult

inputs = {
    "question": list(questions),
    "contexts": list([d.content] for d in ground_truth_docs),
    "answer": list(ground_truth_answers),
    "predicted_answer": rag_answers,
}

evaluation_result = EvaluationRunResult(run_name="pubmed_rag_pipeline", inputs=inputs, results=results)
evaluation_result.score_report()

metrics     score
0  doc_mrr_evaluator  1.000000
1       faithfulness  0.985333
2      sas_evaluator  0.711842

#### Extra: Convert the Report into a Pandas DataFrame

In addition, you can display your evaluation results as a pandas dataframe 👇

In [14]:
results_df = evaluation_result.to_pandas()
results_df

question  \
0   Is higher fibrinogen level independently linke...   
1   Are successional changes in the chicken cecal ...   
2   Does [ ITF increase the transcriptional activi...   
3   Is peer-instructed seminar attendance associat...   
4   Are serum TARC levels strongly correlated with...   
5   Does dexmedetomidine reduce atrial fibrillatio...   
6   Does lidocaine potentiate the deleterious effe...   
7   Does multicenter immunohistochemical ALK-testi...   
8   Does generalizability of trial result to elder...   
9   Does vascular reconstruction play an important...   
10  Is transient receptor potential ankyrin 1 ( TR...   
11  Is incidence of Type 1 Diabetes Increasing in ...   
12  Does transjugular intrahepatic portosystemic s...   
13  Does plasmid pPCP1-derived sRNA HmsA promote b...   
14  Does trichostatin A inhibit Retinal Pigmented ...   
15  Is endo first appropriate in some patients wit...   
16  Do the effects of ifenprodil on the activity o...   
17  Does improving disease incidence estimate in p...   
18  Does unit support protect against sexual haras...   
19  Does treatment with anti-C5a antibody improve ...   
20  Is impaired renal function associated with rec...   
21  Does melatonin prevent radiation-induced oxida...   
22  Is the ADAMTS13-von Willebrand factor axis inv...   
23  Is repeat endoscopic ultrasound fine needle as...   
24  Does tRAIL receptor deletion in mice suppress ...   

                                             contexts  \
0   [Fibrinogen is a coagulation/inflammatory biom...   
1   [Poultry remains a major source of foodborne b...   
2   [To investigate the eff ect of intestinal tref...   
3   [Active engagement in education improves learn...   
4   [This study aims to evaluate the relationship ...   
5   [To evaluate whether the use of intraoperative...   
6   [Local anesthetics are commonly used for the t...   
7   [Detection of anaplastic lymphoma kinase (ALK)...   
8   [In the United States, patients who enroll in ...   
9   [Previous studies have proved the feasibility ...   
10  [Transient receptor potential ankyrin 1 (TRPA1...   
11  [To investigate the recent incidence of T1D in...   
12  [Colorectal resection in cirrhotic patients is...   
13  [The ability of Yersinia pestis to form a biof...   
14  [Proliferative vitreoretinopathy (PVR) is a bl...   
15  [The aims of this study were to determine the ...   
16  [According to reports in the literature, more ...   
17  [In primary care surveillance systems based on...   
18  [Despite concerns about increased sexual haras...   
19  [Patients infected with influenza A(H7N9) viru...   
20  [Atrial fibrillation (AF) and chronic kidney d...   
21  [The aim of this study was to analyze the bioc...   
22  [The ADAMTS13-von Willebrand factor (vWF) axis...   
23  [There is no consensus about the ideal method ...   
24  [Low-grade chronic inflammation is a cardinal ...   

                                               answer  \
0   Higher fibrinogen level is independently linke...   
1   Over the 42 d experiment, the cecal bacterial ...   
2   ITF increases the transcriptional activity of ...   
3   Discussion with well-prepared peers during sem...   
4   Serum TARC levels are well correlated with blo...   
5   These results were similar to those published ...   
6   Our data provide evidence of the detrimental e...   
7   This so-called "ALK-Harmonization-Study" shows...   
8   Results of clinical trials for advanced pancre...   
9   An aggressive approach for stage II pancreatic...   
10  The TRPA1 cation channel was found to be funct...   
11  The incidence of T1D has stopped increasing in...   
12  Portal decompression via TIPS placement may en...   
13  HmsA potentially functions as an activator of ...   
14  Our findings indicate a role of acetylation in...   
15  Previous failed EV should be predictive of poo...   
16  The concomitant administration of certain comm...   
17  Post-stratification using external administrat...

Having our evaluation results as a dataframe can be quite useful. For example, below we can use the pandas dataframe to filter the results to the top 3 best scores for semantic answer similarity (`sas_evaluator`) as well as the bottom 3 👇


In [15]:
import pandas as pd

top_3 = results_df.nlargest(3, "sas_evaluator")
bottom_3 = results_df.nsmallest(3, "sas_evaluator")
pd.concat([top_3, bottom_3])

question  \
21  Does melatonin prevent radiation-induced oxida...   
2   Does [ ITF increase the transcriptional activi...   
0   Is higher fibrinogen level independently linke...   
14  Does trichostatin A inhibit Retinal Pigmented ...   
16  Do the effects of ifenprodil on the activity o...   
15  Is endo first appropriate in some patients wit...   

                                             contexts  \
21  [The aim of this study was to analyze the bioc...   
2   [To investigate the eff ect of intestinal tref...   
0   [Fibrinogen is a coagulation/inflammatory biom...   
14  [Proliferative vitreoretinopathy (PVR) is a bl...   
16  [According to reports in the literature, more ...   
15  [The aims of this study were to determine the ...   

                                               answer  \
21  It was found that radiotherapy increased oxida...   
2   ITF increases the transcriptional activity of ...   
0   Higher fibrinogen level is independently linke...   
14  Our findings indicate a role of acetylation in...   
16  The concomitant administration of certain comm...   
15  Previous failed EV should be predictive of poo...   

                                     predicted_answer  doc_mrr_evaluator  \
21  Yes, melatonin prevents radiation-induced oxid...                1.0   
2   Yes, ITF increases the transcriptional activit...                1.0   
0   Yes, higher fibrinogen level is independently ...                1.0   
14  Yes, trichostatin A (TSA) inhibits Retinal Pig...                1.0   
16  Yes, ifenprodil at a non-active dose (10mg/kg)...                1.0   
15  The phrase "bridges are burned" typically impl...                1.0   

    faithfulness  sas_evaluator  
21           1.0       0.944898  
2            1.0       0.898495  
0            1.0       0.892444  
14           1.0       0.492036  
16           1.0       0.532008  
15           0.8       0.552325

## What's next

🎉 Congratulations! You've learned how to evaluate a RAG pipeline with model-based evaluation frameworks and without any labeling efforts.

If you liked this tutorial, you may also enjoy:
- [Serializing Haystack Pipelines](https://haystack.deepset.ai/tutorials/29_serializing_pipelines)
-  [Creating Your First QA Pipeline with Retrieval-Augmentation](https://haystack.deepset.ai/tutorials/27_first_rag_pipeline)

To stay up to date on the latest Haystack developments, you can [sign up for our newsletter](https://landing.deepset.ai/haystack-community-updates). Thanks for reading!